<a href="https://colab.research.google.com/github/Sheinstein/-Bayesian-Perspective-on-Breast-Cancer-Diagnosis/blob/main/MATH_050_Final_Project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Name :  Salifyanji J Namwila
### Math 050 : Final Project 
### Project Title :  Bayesian Inferences on a Logistic Regression Model for Positive Breast Cancer diagnosis.
### Date: November 15, 2021.

In [116]:
import numpy as np
import pandas as pd
import statsmodels.api as sm
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = "svg"
from pymc3 import *
import arviz as az
from google.colab import drive
drive.mount('/content/drive')
from copy import deepcopy


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Accuracy and Confusion Matrix Implementation

## Coverting Likelihoods to 0 or 1
Wherein 1 reprersents positive breast cancer diagnosis and 0 represents negativer diagnosis

In [117]:
def return_diagnosis(probabilities, threshold):
  for index, likelihood in enumerate(probabilities):
    if likelihood > threshold:
      probabilities[index] = 1
    else:
       probabilities[index] = 0

  return probabilities

## Accuracy and Confusion Matrix

In [118]:
def evaluate(y_actual,y_pred):
    
    false_positve = false_negative = true_positive = true_negative = 0

    # false_positve, false_negative,  true_positive,  true_negative
    false_positive = np.where(((y_actual==0) & (y_pred==1)))[0]
    false_negative = np.where(((y_actual==1 )& (y_pred==0)))[0]
    true_negative = np.where(((y_actual==0) & (y_pred==0)))[0]
    true_positive = np.where(((y_actual==1) & (y_pred==1)))[0]
    
    # false_positve, false_negative,  true_positive,  true_negative
    false_positive = false_positive.size
    false_negative = false_negative.size
    true_positive = true_positive.size
    true_negative = true_negative.size
    
    
    # accuracy
    accuracy = (true_positive + true_negative)/(true_positive + true_negative + false_positive + false_negative)
     
    return false_positive, false_negative, true_positive, true_negative, accuracy

# Experiment 01

In this experiment, whose goal is analogous to Kaiser’s first experiment, in the preprocessing, I drop non-Numerical values, apply mean imputation for missing values, standardize all the continuous predictor variables to allow for a scaled interpretation of results, build a statsmodels classification model (logistic regression), and I finally interpret the results using accuracy, recall and precision functions I define and implement from scratch to report the accuracy and confusion matrix

## Data Pre-Processing
I begin by loading the 'breastcancer.csv' data into a pandas data frame, like so:

In [119]:
# data = pd.read_csv("https://github.com/mokaiser/breast-cancer-diagnosis-a1/blob/master/breastcancer.csv")
data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/breastcancer.csv")
data.head()

id                     name  ...  age  diagnosis
0    ID842302           Glynnis Munson  ...   35          1
1    ID842517              Lana Behrer  ...   27          1
2  ID84300903  Devondra Vanvalkenburgh  ...   31          1
3  ID84348301          Glory Maravalle  ...   49          1
4  ID84358402           Mellie Mccurdy  ...   20          1

[5 rows x 13 columns]

### Data Cleaning
The missing radius data needs to be filled in (not just dropped) by filling in the mean radius. Let's check the average radius by diagnosis.

In [120]:
# calculate the average radius size by diagnosis (0 or 1)
experiment1_data = deepcopy(data)
experiment1_data.groupby('diagnosis')["radius"].mean()

diagnosis
0    12.340825
1    17.896629
Name: radius, dtype: float64

In [121]:
# create a function that imputes average radius into missing values

def impute_radius(cols):
    radius = cols[0]
    diagnosis = cols[1]
    
    # if value in radius column is null
    if pd.isnull(radius):
        
        # if woman is diagnosed with breast cancer
        if diagnosis == 1:
            return 17
        # if woman was not diagnosed with breast cancer
        else:
            return 12
    # when value in radius column is not null
    else:
        # return that same value
        return radius

In [122]:
experiment1_data['radius'] = experiment1_data[['radius', 'diagnosis']].apply(impute_radius, axis = 1)

### Dropping non-numerical columns

In [123]:
# dropping categorical variables

experiment1_data.drop(['id', 'name'], axis = 1, inplace = True)
experiment1_data.head()

radius  texture  perimeter  ...  fractal_dimension  age  diagnosis
0   17.00    10.38     122.80  ...            0.07871   35          1
1   20.57    17.77     132.90  ...            0.05667   27          1
2   19.69    21.25     130.00  ...            0.05999   31          1
3   17.00    20.38      77.58  ...            0.09744   49          1
4   20.29    14.34     135.10  ...            0.05883   20          1

[5 rows x 11 columns]

### Standardizing Predictor Variables
Standardization is the process of putting different variables on the same scale. In regression analysis, there are some scenarios where it is crucial to standardize your independent variables or risk obtaining misleading results.

One way of standardizing is using z-score. Here we **standarize**  a variable, so that a change in $1$ corresponds to about 1 standard deviation and their mean is zero. If $x$ is some variable, the standardized variable or $z$-score is 
\begin{equation}
z_x = \frac{x-\bar{x}}{{\rm std}(x)}. 
\end{equation}

If we standardize $x$ then an increase of one on the standarized scale corresponds to an increase one one standard deviation on the original scale. This is useful if we have multiple predictors

In [124]:
# standardize predictor variables 
experiment1_data["z_radius"] = (experiment1_data["radius"].values - np.mean(experiment1_data["radius"].values ))/np.std(experiment1_data["radius"].values )
experiment1_data["z_texture"] = (experiment1_data["texture"].values - np.mean(experiment1_data["texture"].values ))/np.std(experiment1_data["texture"].values )
experiment1_data["z_perimeter"] = (experiment1_data["perimeter"].values - np.mean(experiment1_data["perimeter"].values ))/np.std(experiment1_data["perimeter"].values )
experiment1_data["z_area"] = (experiment1_data["area"].values - np.mean(experiment1_data["area"].values ))/np.std(experiment1_data["area"].values )
experiment1_data["z_smoothness"] = (experiment1_data["smoothness"].values - np.mean(experiment1_data["smoothness"].values ))/np.std(data["smoothness"].values )
experiment1_data["z_compactness"] = (experiment1_data["compactness"].values - np.mean(experiment1_data["compactness"].values ))/np.std(experiment1_data["compactness"].values )
experiment1_data["z_concavity"] = (experiment1_data["concavity"].values - np.mean(experiment1_data["concavity"].values ))/np.std(experiment1_data["concavity"].values )
experiment1_data["z_symmetry"] = (experiment1_data["symmetry"].values - np.mean(experiment1_data["symmetry"].values ))/np.std(experiment1_data["symmetry"].values )
experiment1_data["z_fractal_dimension"] = (experiment1_data["fractal_dimension"].values - np.mean(experiment1_data["fractal_dimension"].values ))/np.std(experiment1_data["fractal_dimension"].values )
experiment1_data["z_age"] = (experiment1_data["age"].values - np.mean(experiment1_data["age"].values ))/np.std(experiment1_data["age"].values )
# note that diagnosis remains unchanged. But for formatting purposes add the z_diagnosis as last column
experiment1_data["z_diagnosis"] = experiment1_data["diagnosis"]

# drop unstandardized values
experiment1_data = experiment1_data.drop(columns =["radius"])
experiment1_data = experiment1_data.drop(columns =["texture"])
experiment1_data = experiment1_data.drop(columns =["perimeter"])
experiment1_data = experiment1_data.drop(columns =["area"])
experiment1_data = experiment1_data.drop(columns =["smoothness"])
experiment1_data = experiment1_data.drop(columns =["compactness"])
experiment1_data = experiment1_data.drop(columns =["concavity"])
experiment1_data = experiment1_data.drop(columns =["symmetry"])
experiment1_data = experiment1_data.drop(columns =["fractal_dimension"])
experiment1_data = experiment1_data.drop(columns =["age"])
experiment1_data = experiment1_data.drop(columns =["diagnosis"])

experiment1_data.head()

z_radius  z_texture  z_perimeter  ...  z_fractal_dimension     z_age  z_diagnosis
0  0.785123  -2.073335     1.269934  ...             2.255747 -0.328668            1
1  1.836899  -0.353632     1.685955  ...            -0.868652 -0.917218            1
2  1.577637   0.456187     1.566503  ...            -0.398008 -0.622943            1
3  0.785123   0.253732    -0.592687  ...             4.910919  0.701295            1
4  1.754406  -1.151816     1.776573  ...            -0.562450 -1.432199            1

[5 rows x 11 columns]

### Dropping Obeserved y

Next, I drop all non numerical columns, i.e the 'id' and 'name' columns. I also drop all columns with 'Nan' values as the Variance Inflation Factor(described later) cannot be calculated with nan values

In [125]:
# drop observed y's
exprement1_data_X = experiment1_data.drop('z_diagnosis', axis = 1)
exprement1_diagnosis_y = experiment1_data['z_diagnosis']
exprement1_diagnosis_y.head()

0    1
1    1
2    1
3    1
4    1
Name: z_diagnosis, dtype: int64

### Data Splitting

Now that the data set has been cleaned, it time to split it into training set and test set. The split ratio used is 70% training set and 30% test set with a random seed, to allow for reproducibility and debugging purposes.

In [126]:
from sklearn.model_selection import train_test_split

experiment1_data_X_train, experiment1_data_X_test, experiment1_diagnosis_y_train,experiment1_diagnosis_y_test = train_test_split(exprement1_data_X, exprement1_diagnosis_y, test_size = 0.3, random_state = 11111)
experiment1_data_X_train.head()

z_radius  z_texture  ...  z_fractal_dimension     z_age
224 -0.313790  -0.528162  ...            -0.858729 -1.652905
215 -0.139967  -0.549106  ...             0.901935  0.039176
463 -0.805797  -0.216335  ...            -0.596472  0.186314
94   0.213570   0.125743  ...             0.006009  0.922002
274  1.059115   1.207830  ...            -1.091216  0.039176

[5 rows x 10 columns]

## Data Training

### Fiitng to Statsmodel Logit Regression model

In [127]:
model0 = sm.Logit(experiment1_diagnosis_y_train, sm.add_constant(experiment1_data_X_train.to_numpy()))
results0 = model0.fit()
print(results0.summary())

Optimization terminated successfully.
         Current function value: 0.137692
         Iterations 10
                           Logit Regression Results                           
Dep. Variable:            z_diagnosis   No. Observations:                  398
Model:                          Logit   Df Residuals:                      387
Method:                           MLE   Df Model:                           10
Date:                Sat, 20 Nov 2021   Pseudo R-squ.:                  0.7947
Time:                        00:00:40   Log-Likelihood:                -54.802
converged:                       True   LL-Null:                       -266.94
Covariance Type:            nonrobust   LLR p-value:                 6.359e-85
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.7472      0.520     -1.436      0.151      -1.767       0.273
x1             2.3263      1

## Evaluation


### Interpretation of Pseudo $R^2$
Pseudo $R^2$ compares how likely it is to see the particular sequance of $y$ values under the model, vs. how likely it would be to see them if the chance to get $y=1$ did not depend on $x$:
\begin{equation}
{\rm pseudo}\, R^2 = 1- \frac{\ln( \text{chance to see $y_1,y_2,\dots,y_n$ given our model})}{\ln (\text{chance to see $y_1,y_2,\dots,y_n$ given $x$ has no effect})}
\end{equation}

**Overall, this tells us how good our model is at predicting the $y$ values**.

**Analysis**
Pseudo $R^2$  value of the model is $0.7947$, which is very large(close to one).A rule of thumb that I found to be quite helpful is that a  Pseudo $R^2$ ranging from 0.2 to 0.4 indicates very good model fit. As such, the model mentioned above with a Pseudo $R^2$ is not just a good fit but also an excellent fit. 

The goodness of the model is also reinforced by the value of $p-value$, which is significantly below the standard threshold 0.05.

[GAJ Hermmet (2018) `Likelikood-Based Pseudo $R^2$ `; `https://www.google.com/url?sa=t&rct=j&q=&esrc=s&source=web&cd=&ved=2ahUKEwi2huSg26X0AhUkgnIEHQjQCzoQFnoECDgQAQ&url=https%3A%2F%2Fjournals.sagepub.com%2Fdoi%2Fpdf%2F10.1177%2F0049124116638107&usg=AOvVaw21ZvFnSx7QFLoninHLfyrR`]



### Recall, Precision, Accuracy
Classification report checks precision, recall, and f1 score of the model. The support is the number of samples of the true response that lie in that class

#### Precision 
Precision quantifies the number of positive class predictions that actually belong to the positive class.

$Precision = True Positives / (True Positives + False Positives)$

#### Recall 
Recall quantifies the number of positive class predictions made out of all positive examples in the dataset.

$Recall = True Positives  / (True Positives + False Negatives)$

In [153]:
X_test_imput = sm.add_constant(experiment1_data_X_test.to_numpy()) # add a column of all 
y_pred0 = results0.predict(X_test_imput)


model0_diagnosis = return_diagnosis(y_pred0, 0.75)

# obtain accuracy
FP, FN, TP,TN, model0_accuracy_score =  evaluate(experiment1_diagnosis_y_test, model0_diagnosis)

print("FP:", FP)
print("FN: ", FN)
print("TP: ", TP)
print("TN", TN)
print("Precision: ", TP/(TP+FP)*100)
print("Recall: ", TP/(TP+FN)*100)
print("accuracy: ", model0_accuracy_score*100)


FP: 0
FN:  5
TP:  50
TN 116
Precision:  100.0
Recall:  90.9090909090909
accuracy:  97.07602339181285


## Summary

For our purposes, this presents a great model. It has very high precion, recall and accuracy scores. All of which are higher than Kaiser Moo's for the same experiment  just using the sklearn library. Her report of precision, recall, and acuracy were $93%$ , $90.7%$,and  $90%$.

This is a rather more informative report as it tells us how good of a fit oiur model is to the data by reporting the $Psuedo r^2$ value. That wy we would not be blindly reporting diagnoses, especially false Negatives(which present more cost) but also scale the posibility while taking into account the relaibility of the model.

### Is that all?
Not Quite Unfortunately.
Sometimes Complex models tends to overfit data.  A good practice is to train a model with sizeable number of features. If at all certain features do not affect the precdictions that much, uts best to truncate them. The next experimnet tries to come up with a less complex model by eliminatiinhg highly correlated predictors.

# Experiment 02

## Dropping non-numerical and 'Nan' columns
Next, I drop all non numerical columns, i.e the 'id' and 'name' columns. I also drop all columns with 'Nan' values as the Variance Inflation Factor(described later) cannot be calculated with nan values

In [128]:
# drop non-numerical columns
experiment2_data = deepcopy(data)
experiment2_data.dropna(inplace=True) # vif can't be calculated with nan values!
experiment2_data = experiment2_data._get_numeric_data() # drop non-numeric cols aka categorical vars
experiment2_data.head()

radius  texture  perimeter  ...  fractal_dimension  age  diagnosis
1    20.57    17.77      132.9  ...            0.05667   27          1
2    19.69    21.25      130.0  ...            0.05999   31          1
4    20.29    14.34      135.1  ...            0.05883   20          1
6    18.25    19.98      119.6  ...            0.05742   38          1
10   16.02    23.24      102.7  ...            0.05697   51          1

[5 rows x 11 columns]

## Variance Inflation Factor (VIF)

The variance inflation factor is a measure for the increase of the variance of the parameter estimates if an additional variable, given by exog_idx is added to the linear regression. It is a measure for multicollinearity of the design matrix, exog.

One recommendation is that if VIF is greater than 5, then the explanatory variable given by exog_idx is highly collinear with the other explanatory variables, and the parameter estimates will have large standard errors because of this.



In [129]:
from statsmodels.stats.outliers_influence import variance_inflation_factor

# Indicate which variables to compute VIF
X = experiment2_data[['radius','texture','perimeter', 'area', 'smoothness', 'compactness',
        'concavity', 'symmetry', 'fractal_dimension', 'age']]

# add intercept
X['intercept'] = 1

 # Compute VIF
vif = pd.DataFrame()
vif["variables"] = X.columns
vif["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]
vif


variables          VIF
0              radius  2691.890851
1             texture     1.190516
2           perimeter  3398.214223
3                area    69.009830
4          smoothness     2.255147
5         compactness    21.960456
6           concavity    12.263368
7            symmetry     1.495297
8   fractal_dimension     4.235412
9                 age     1.021168
10          intercept  1535.634271


From statsmodels:

"If VIF > 5, then the explanatory variable is highly collinear with the other explanatory variables, and the parameter estimates will have large standard errors because of this."

It seems that radius, perimeter, area, compactness, and concavity are above the threshold (VIF > 5). This means we should drop these columns as they will cause a negative effect on our logistic regression model.

From Investopedia:

"It is better to use independent variables that are not correlated when building multiple regression models that use two or more variables."

In [130]:
# Drop all columns with VIF > 5
experiment2_data.drop(columns=['radius', 'perimeter', 'area', 'compactness','concavity'], inplace=True)
experiment2_data.head()

texture  smoothness  symmetry  fractal_dimension  age  diagnosis
1     17.77     0.08474    0.1812            0.05667   27          1
2     21.25     0.10960    0.2069            0.05999   31          1
4     14.34     0.10030    0.1809            0.05883   20          1
6     19.98     0.09463    0.1794            0.05742   38          1
10    23.24     0.08206    0.1528            0.05697   51          1

## Standardizing Predictor Variables
Standardization is the process of putting different variables on the same scale. In regression analysis, there are some scenarios where it is crucial to standardize your independent variables or risk obtaining misleading results.

One way of standardizing is using z-score. Here we **standarize**  a variable, so that a change in $1$ corresponds to about 1 standard deviation and their mean is zero. If $x$ is some variable, the standardized variable or $z$-score is 
\begin{equation}
z_x = \frac{x-\bar{x}}{{\rm std}(x)}. 
\end{equation}

If we standardize $x$ then an increase of one on the standarized scale corresponds to an increase one one standard deviation on the original scale. This is useful if we have multiple predictors

In [131]:
# standardize predictor variables 
experiment2_data["z_texture"] = (experiment2_data["texture"].values - np.mean(experiment2_data["texture"].values ))/np.std(experiment2_data["texture"].values )
experiment2_data["z_smoothness"] = (experiment2_data["smoothness"].values - np.mean(experiment2_data["smoothness"].values ))/np.std(experiment2_data["smoothness"].values )
experiment2_data["z_symmetry"] = (experiment2_data["symmetry"].values - np.mean(experiment2_data["symmetry"].values ))/np.std(experiment2_data["symmetry"].values )
experiment2_data["z_fractal_dimension"] = (experiment2_data["fractal_dimension"].values - np.mean(experiment2_data["fractal_dimension"].values ))/np.std(experiment2_data["fractal_dimension"].values )
experiment2_data["z_age"] = (experiment2_data["age"].values - np.mean(experiment2_data["age"].values ))/np.std(experiment2_data["age"].values )
experiment2_data["z_diagnosis"] = experiment2_data["diagnosis"]

# drop unstandardized values
experiment2_data = experiment2_data.drop(columns =["texture"])
experiment2_data = experiment2_data.drop(columns =["smoothness"])
experiment2_data = experiment2_data.drop(columns =["symmetry"])
experiment2_data = experiment2_data.drop(columns =["fractal_dimension"])
experiment2_data = experiment2_data.drop(columns =["age"])
experiment2_data = experiment2_data.drop(columns =["diagnosis"])

experiment2_data.head()

z_texture  z_smoothness  ...     z_age  z_diagnosis
1   -0.352722     -0.761682  ... -0.902473            1
2    0.456740      1.218336  ... -0.607715            1
4   -1.150554      0.477621  ... -1.418298            1
6    0.161333      0.026024  ... -0.091890            1
10   0.919622     -0.975135  ...  0.866072            1

[5 rows x 6 columns]

## Dropping Observed y
It is important to detach the observed values of y, in this case the true diagnosis from all other  data features the goal is for us to learn betas(wieghts) that result in those diagnosis results.

In [132]:
# drop observed y's
X = experiment2_data.drop('z_diagnosis', axis = 1)
Y = experiment2_data['z_diagnosis']
X.head()

z_texture  z_smoothness  z_symmetry  z_fractal_dimension     z_age
1   -0.352722     -0.761682    0.159725            -0.914048 -0.902473
2    0.456740      1.218336    1.206990            -0.185766 -0.607715
4   -1.150554      0.477621    0.147500            -0.440226 -1.418298
6    0.161333      0.026024    0.086376            -0.749526 -0.091890
10   0.919622     -0.975135   -0.997563            -0.848239  0.866072

## Data Splitting
Now that the data set has been cleaned, it time to split it into training set and test set. The split ratio used is 70% training set and 30% test set.


In [133]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size = 0.3, random_state = 10001)
X_train.head()

z_texture  z_smoothness  z_symmetry  z_fractal_dimension     z_age
502  -0.689998      1.712146    0.693545             1.158923  1.676655
79   -0.299223      0.401161   -0.223321            -0.190153  0.939761
205  -0.606260     -0.441502   -0.728616            -0.214283 -0.755094
174  -0.962145     -0.508405    0.632421            -0.238413 -1.197230
126   1.256898     -0.137252   -0.048098             0.101598 -0.534026

# Data Training

### Fitting to a Logistic Regression Model 

In [134]:
model1 = sm.Logit(y_train, sm.add_constant(X_train.to_numpy()))
results1 = model1.fit()
print(results1.summary())

Optimization terminated successfully.
         Current function value: 0.386565
         Iterations 7
                           Logit Regression Results                           
Dep. Variable:            z_diagnosis   No. Observations:                  348
Model:                          Logit   Df Residuals:                      342
Method:                           MLE   Df Model:                            5
Date:                Sat, 20 Nov 2021   Pseudo R-squ.:                  0.4033
Time:                        00:01:27   Log-Likelihood:                -134.52
converged:                       True   LL-Null:                       -225.43
Covariance Type:            nonrobust   LLR p-value:                 2.186e-37
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         -1.1845      0.180     -6.574      0.000      -1.538      -0.831
x1             1.3591      0.

## Evaluation

### Pseudo $R^2$
Again I cannot stress enough the gravity of reporting  how good our model is at predicting the $y$ values** - Pseudo $R^2$.
 
 So, after droping the multicolinear predictors, and fitting the model with the net predictors, we observe that the Pseudo $R^2$ drops. This should not be surprising as we by reducing number of predictors of the model to reduce overfitting we buy simplicity and loose some accuracy.
 However, a like ealrier alluded, this still presents an excellent Pseudo $R^2$. So the model is a good fit. Let take a look at the precision, recall and accuracy scores. Remember we care so much about false negatives, as they are the most coslty. So, if we see alarming numbers, we are bound to imcrease complexity to until we reach a reasonable optimum.

### Recall, Precision, Accuracy

In [152]:
#  Evaluation model from experiment 2 
X_test_new = sm.add_constant(X_test.to_numpy()) # add a column of all 
y_pred1 = results1.predict(X_test_new)
y_pred1

model1_diagnosis = return_diagnosis(y_pred1, 0.5122)

# obtain accuracy
FP, FN, TP,TN, model1_accuracy_score =  evaluate(y_test, model1_diagnosis)

print("FP:", FP)
print("FN: ", FN)
print("TP: ", TP)
print("TN", TN)
print("Precision: ", TP/(TP+FP)*100)
print("Recall: ", TP/(TP+FN)*100)
print("accuracy: ", model1_accuracy_score*100)


FP: 8
FN:  20
TP:  36
TN 86
Precision:  81.81818181818183
Recall:  64.28571428571429
accuracy:  81.33333333333333


### Evaluation Summary

From the perspective of Pseudo $R^2$ this still presents a great model evewn though there has been a drastic drop of the value by ... 
However, Looking at the number of False Ngative now, I believe this model is not ideal in such a sensitive problem.

For our purposes, this does **NOT** present a great model. It has a quite good precion, **red light** recall and not too bad accuracy scores. Compared to  Kaiser Moo's equivalent second experiement just using the sklearn library, her report of precision, recall, and acuracy were $84.6%$ , $68.1%$,and  $66%$.

Her model has 36 False Negatives, while this model has 20 False Negatives. Could we do better by adding some interactions? Which interactions?




### Evaluation of largest factor in determining whether a patient with a breast tumor has breast cancer

## Answer:

####Part A:

What is the largest factor in determining whether a patient with a breast tumor has breast cancer? What does this tell us about the association between the predictors and breast cancer diagnosis?




To find the largest factor in determining largest factor in determining whether a patient with a breast tumor has breast cancer, it is logical to take the logistic regression coefficients(other than the constant term) and divide them by 4 to get the upper bound of the predictive difference corresponding to a unit difference in the predictor variable,say x.

Dividing coefficients of x's by 4: 

* $\hat{\beta}_1 = 0.339775 $ : A difference of 1 standard deviation in tumor texture between patients with all other tumor characteristcs being the same being the same corresponds to no more than $33.9775\%$ in positive cancer diagnosis ( posiitvie with cancer).


Do the same for all other predictors ...

*  $\hat{\beta}_2 = 0.475975 $ : A difference  of 1 standard deviation in tumor smoothness between patients with all other tumor characteristics being the same coreresponds to no more than $47.5975\%$ in positive cancer diagnosis(found with cancer). 

* $\hat{\beta}_3 = 0.1158 $: A difference of 1 standard deviation in tumour symmetry between patients with all other tumor characteristics being the same coreresponds to no more than $11.58\%$ in positive cancer diagnosis (diagnosed with cancer)

* $\hat{\beta}_4 = -0.385175 $: A difference of 1 standard deviation in tumor fractal dimension between patients with all other tumor characteristics being the same coreresponds to no more than $-38.5175\% $ in negative cancer diagnosis ( no cancer).

* $\hat{\beta}_5 = -0.0435 $: A difference of 1 standard deviation in age between patients with all other tumor characteristics being the same coreresponds to no more than $ -4.35\%$  in negative cancer diagnosis ( no cancer).

After the above evaluation, it is obvious that when patients differ only in tumor smoothness by 1, all else being equal, the upper bound of the predictive difference in  positive diagnosis for breast cancer can go upto and including $47.5975\%$. Ergo, smoothness of tumor  has the largest factor in determining whether a patient is diagnosed with breast cancer followed by fractal dimension, and then tumor texture.


#### Part B:

The likelihood of positive cancer diagnosis between patients that have tumors that differ only smoothness has the highest upper bound predictive range, followed by patients that with tumors that differ only in  fractal dimensions, followed by patients with tumors that differe only in texture.Symmetry and age have the least upper bound predictive range so It wouldnt be so  useful to try evaluation interaction terms involving them.

###**Interesting Discovery**
 Age has the least upper bound predictive range. Meaning that the diffrence in age does not affect the diagnosis result by that much. Wow!

**So then just how do the three most influencial predictors, smoothness, fractal dimension, texture,  interact with each other? Enter Bayesian Inferences.**


.


### Bayesian inference with many predictors

Since this model has a number of predictors and there is a great deal of uncertainty about many of them, it may be important to propogate that to our predictions. Below, I show how to implement Bayesian infernce on this model. When dealing with models that have more than just a few predictors, it can become difficult and time-consuming to set weakly informative priors. We would have to go through each parameters and think about our prior beliefs. Moreover, with many predictors, the Markov chain monte carlo simulations (the algorithm which draws samples from the posterior) can be unstable and will easily crash if our priors are too wide. 

One solution is to runs stats models to get some estimates of the parameters and then use the means and standard errors to set our priors. In order to keep our priors vague, we can multiple the standard errors by a factor, say $2$.

 **It is important to note that this approach is not strictly Bayesian**. Some would argue it is not the correct way to apply Bayesian statistics. However, in practice this is one way to make Bayesian inference useable on large models. 

In [137]:
# add dummie variables
X_train_tild = sm.add_constant(X_train.to_numpy()) # add a column of all 1s
print(X_train_tild.shape[1])

log_model1 = Model()

with log_model1:
  beta  = Normal("beta", results1.params, 2*results1.bse, shape=6)
  intercept = Normal("intercept",0,3)
  likelihood = Bernoulli("y", math.sigmoid(intercept + math.dot(X_train_tild, beta)), observed=y_train)

  trace1 = sample(1000,cores=3)


6


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:12: FutureWarning: In v4.0, pm.sample will return an `arviz.InferenceData` object instead of a `MultiTrace` by default. You can pass return_inferencedata=True or return_inferencedata=False to be safe and silence this warning.
  if sys.path[0] == '':
Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (3 chains in 3 jobs)
NUTS: [intercept, beta]


Sampling 3 chains for 1_000 tune and 1_000 draw iterations (3_000 + 3_000 draws total) took 14 seconds.


In [96]:
az.plot_pair(trace0,figsize=(7,7),textsize=5);

Got error No model on context stack. trying to find log_likelihood in translation.
/usr/local/lib/python3.7/dist-packages/arviz/data/io_pymc3_3x.py:102: FutureWarning: Using `from_pymc3` without the model will be deprecated in a future release. Not using the model will return less accurate and less useful results. Make sure you use the model argument or call from_pymc3 within a model context.
  FutureWarning,


### Evaluation of Predictor Interactions

KEY:
* $\hat{\beta}_1 $ represents the coefficient for z_texture

* $\hat{\beta}_2 $ represents the coefficient for z_smoothness

* $\hat{\beta}_4 $ represents the coefficient for z_fractal dimension

To save my words, I highlight only these as they are the most important features that affect the diagnosis.

Now lets take a look at the scatterplots of 

$\hat{\beta}_2 $ vs $\hat{\beta}_1 $ :
We see that is almost a nomrmal distribution. However, exaclty.  There seems to be a positive corealtion. between the two in the posterior i.e if we have larger values of $\beta_1$, the value of  $\beta_2$ is more likely to be larger as well. More clearly,  if we have larger standard deiations of tumor texture , the standard deviations of  smoothnes  is more likely to be larger as well.

On the contrary, for  $\beta_2$ and $\beta_4$ there seem s to to be a pretty strong negative correlation in the posterior i.e. if we have a larger value of smoothness, the value of fractal dimension is more likely to be small and vise versa. The scatter plot shows that it is likely that there is either a larger effect of smoothness data set and a smaller effect of fractal dimension data set or vise-versa.

Lastly, for $\beta_1$ and $\beta_4$ there seems to be a normal distribution and less of a negative correlation.
 


# Experiment 03: Adding Interactions

We consider adding some interaction terms between  the most important predictors in the model.


In [138]:
# copy X into new DataFrame
X_int = deepcopy(X_train)
y_int = deepcopy(y_train)

# add interaction term to training set
X_int["z_smooth*z_fract_dim"] = X_int["z_smoothness"] * X_int["z_fractal_dimension"]
X_int["z_smooth*z_text"] = X_int["z_smoothness"] * X_int["z_texture"]
X_int["z_fract_dim*z_text"] = X_int["z_fractal_dimension"] * X_int["z_texture"]

X_int.head()


z_texture  z_smoothness  ...  z_smooth*z_text  z_fract_dim*z_text
502  -0.689998      1.712146  ...        -1.181377           -0.799654
79   -0.299223      0.401161  ...        -0.120037            0.056898
205  -0.606260     -0.441502  ...         0.267665            0.129911
174  -0.962145     -0.508405  ...         0.489159            0.229388
126   1.256898     -0.137252  ...        -0.172511            0.127698

[5 rows x 8 columns]

### Computing VIF with interaction Terms


In [139]:
# Indicate which variables to compute VIF
X_int = X_int[['z_texture','z_smoothness','z_symmetry', 'z_fractal_dimension', 'z_age', 'z_smooth*z_text',"z_smooth*z_fract_dim","z_fract_dim*z_text" ]]

# add intercept
#X_int['intercept'] = 1

 # Compute VIF
vif = pd.DataFrame()
vif["variables_int"] = X_int.columns
vif["VIF_int"] = [variance_inflation_factor(X_int.values, i) for i in range(X_int.shape[1])]
vif


variables_int   VIF_int
0             z_texture  1.050000
1          z_smoothness  1.710128
2            z_symmetry  1.361597
3   z_fractal_dimension  1.429444
4                 z_age  1.034508
5       z_smooth*z_text  1.611219
6  z_smooth*z_fract_dim  1.079794
7    z_fract_dim*z_text  1.568373

Since the VIF score for all interaction terms  are well below the recommended 5, no need to discard them.

###Training Data with Interaction Terms

In [140]:
model2 = sm.Logit(y_int, sm.add_constant(X_int.to_numpy()))
results2 = model2.fit()
print(results2.summary())

Optimization terminated successfully.
         Current function value: 0.335594
         Iterations 8
                           Logit Regression Results                           
Dep. Variable:            z_diagnosis   No. Observations:                  348
Model:                          Logit   Df Residuals:                      339
Method:                           MLE   Df Model:                            8
Date:                Sat, 20 Nov 2021   Pseudo R-squ.:                  0.4819
Time:                        00:05:17   Log-Likelihood:                -116.79
converged:                       True   LL-Null:                       -225.43
Covariance Type:            nonrobust   LLR p-value:                 1.434e-42
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         -1.0349      0.221     -4.693      0.000      -1.467      -0.603
x1             1.4894      0.

### Pseudo $R^2$ with Interaction Terms

After adding interactions between the three most important prectors, our Pseudo $R^2$ improves from $0.4033$ to $ 0.4819$ an imporovemnent of $+0.0786$. 

A good question then would be: Is it worth adding three interaction terms (thereby making the model more complex) and only having it improve by $+0.0786$. ? 

Well, I say let the change in the  number of False Negative decide. Recall that we have 20 False Negatives withouth interaction i.e in Experiement two. So , on to Evaluation.

##Evaluation

### Precision, Recall, Accuracy

In [144]:
# copy X into new DataFrame
X_test_int = deepcopy(X_test)
y_test_int = deepcopy(y_test)

# add interaction terms to the test set
X_test_int["z_smooth*z_fract_dim"] = X_test["z_smoothness"] * X_test["z_fractal_dimension"]
X_test_int["z_smooth*z_text"] = X_test["z_smoothness"] * X_test["z_texture"]
X_test_int["z_fract_dim*z_text"] = X_test["z_fractal_dimension"] * X_test["z_texture"]

X_test_int.head()

z_texture  z_smoothness  ...  z_smooth*z_text  z_fract_dim*z_text
134   0.610259     -0.000259  ...        -0.000158           -0.477485
292  -0.759779      0.493551  ...        -0.374990           -0.643859
268  -0.715584     -0.004241  ...         0.003035            0.493967
235   0.456740     -0.286987  ...        -0.131079           -0.249161
529  -1.359898      1.250195  ...        -1.700137           -1.564084

[5 rows x 8 columns]

In [154]:
X_test_new2 = sm.add_constant(X_test_int.to_numpy()) # add a column of all 
y_pred2 = results2.predict(X_test_new2)
#print(y_pred1)

model2_diagnosis = return_diagnosis(y_pred2, 0.55)

# obtain accuracy
FP, FN, TP,TN, model2_accuracy_score =  evaluate(y_test_int, model2_diagnosis)
print("FP:", FP)
print("FN: ", FN)
print("TP: ", TP)
print("TN", TN)
print("Precision: ", TP/(TP+FP)*100)
print("Recall: ", TP/(TP+FN)*100)
print("accuracy: ", model2_accuracy_score*100)


FP: 17
FN:  10
TP:  46
TN 77
Precision:  73.01587301587301
Recall:  82.14285714285714
accuracy:  82.0


## Summary

Wow! Our False Negatives Drop by Half: from $20$ to $10$ only. Even though this does not compra the the model in Experiement 1, it still does have a lot to say about the informativeness of the. most  interaction  terms, which could be a very creative way of engineering our data in circumstances where we have a shortage of data.

How do precision, recall and accuracy compare to to the model in experiment 2?


```
Experiment 2
FP: 8
FN:  20
TP:  36
TN 86
Precision:  81.81818181818183
Recall:  64.28571428571429
accuracy:  81.33333333333333

```


```
Experiment 3:
FP: 17
FN:  10
TP:  46
TN 77
Precision:  73.01587301587301
Recall:  82.14285714285714
accuracy:  82.0
```
We see that while precision drops in experiment 3, both recall and accuracy in improve, with recall exhibiting a large jump from $64.285\%$ to $82.14\%$


# Moral

There is no such thing as free lunch. As many of us researchers strive to alleviate the number of deaths from breast cancer, we are constantly making trade offs between complexity, data availability et cetera. In all cases, I propose that if we have to make this tough decision and we will have to,that  we uplhold models  that favor the least number of false negative diagnoses than false positives.For, it is better to make $1000$ trips for $3$ years, or for ever, to a hospital and later realize you were in fact not positive than to  stay home thinking you had a benign cyst, only to discover you not only have cancer but it is now stage $4$ and you'll have to die in the next few months, leaving your loved ones, kids, and family in grave pain because breast cancer is that fucking deadly.

Let us build  models to save patients from breast cancer through early diagnosis!
Please and Thank you